In [1]:
import sys; sys.path.append('..')
from philadata import *

In [2]:
def get_geojson_warddiv(fn='ward_divisions.geojson', force=False):
    fn=os.path.join(path_philadata_data, fn) if not os.path.isabs(fn) else fn
    url=URLS.get('ward_divisions')
    if force or not os.path.exists(fn):
        data = requests.get(url)
        with open(fn,'wb') as of: 
            of.write(data.content)

    # load        
    with open(fn) as f:
        jsond=json.load(f)
        
    # # anno
    # for d in jsond['features']:
    #     d['id'] = str(d['properties']['c_ar'])
    #     d['properties']['arrond_id'] = d['id']
    
    return jsond


In [5]:
divnums=set()
for d in get_geojson_warddiv()['features']:
    divnums.add(d['properties']['DIVISION_NUM'])

In [20]:
@lru_cache(maxsize=None)
def get_center_lat_lon():
    xl=[]
    yl=[]
    for d in get_geojson_warddiv()['features']:
        for x,y in iter_minmaxs(d['geometry']['coordinates']):
            xl.append(x)
            yl.append(y)
    center_lon,center_lat=np.median(xl),np.median(yl)
    return (center_lat,center_lon)

In [21]:
df=precinct_data()
geo=get_geojson_warddiv()

In [22]:
# geo

In [25]:
px.choropleth_mapbox(
    df,
    locations='prec_20',
    geojson=geo,
    featureidkey='properties.DIVISION_NUM',
    color='PRESIDENT OF THE UNITED STATES-DEM_BERNIE SANDERS',
    mapbox_style="carto-positron",
    center={'lat':center_lat, 'lon':center_lon},
    # zoom=9
)